In [224]:
import pandas as pd
import json
import math
import re

# Función para agrupar mensajes de Remitentes

In [225]:
def agrupar_remitentes(texto_in):
    # Dividir el texto en líneas
    lineas = texto_in.strip().split('\n')

    # Procesar las líneas para agrupar los mensajes por remitente
    texto_out = ""
    ultimo_remitente = ""
    timestamp_actual = ""

    for linea in lineas:
        # Verificar si la línea tiene un remitente (es decir, si es un nuevo mensaje)
        if re.match(r"\[\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2}:\d{2} [a.p].m.\] \w+:", linea):
            timestamp, remitente, mensaje = re.match(r"(\[\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2}:\d{2} [a.p].m.\]) (\w+): (.*)", linea).groups()
            # Si el remitente es diferente al último, se inicia un nuevo mensaje
            if remitente != ultimo_remitente:
                texto_out += f"{timestamp} {remitente}: {mensaje}\n"
                ultimo_remitente = remitente
                timestamp_actual = timestamp
            else:
                # Añadir el mensaje actual al último mensaje del mismo remitente
                texto_out = texto_out.strip() + "\n" + mensaje + "\n"
        else:
            # Si la línea no tiene remitente, se añade al mensaje actual
            texto_out = texto_out.strip() + "\n" + linea.strip() + "\n"

    texto_out = texto_out.strip()

    return texto_out

### Prueba

In [176]:
texto_in = """
[30/08/22, 4:11:28 p.m.] CarmenQ: Pues eso es bueno
[30/08/22, 4:11:33 p.m.] CarmenQ: Así te llenas cool
[30/08/22, 4:11:51 p.m.] Sebas: Pues si
[30/08/22, 4:11:55 p.m.] Sebas: Ya me la terminé
Ya voy a regresar
[30/08/22, 4:12:15 p.m.] CarmenQ: Que bueno
Ok amor
[30/08/22, 4:12:25 p.m.] CarmenQ: Mucha suerte
La verdad es que tengo mucho sueño
[30/08/22, 4:12:33 p.m.] Sebas: Gracias amorcito
Te amo mucho
[30/08/22, 4:12:40 p.m.] CarmenQ: Yo a ti
"""

# Imprimir el texto transformado
print(agrupar_remitentes(texto_in))

[30/08/22, 4:11:28 p.m.] CarmenQ: Pues eso es bueno
Así te llenas cool
[30/08/22, 4:11:51 p.m.] Sebas: Pues si
Ya me la terminé
Ya voy a regresar
[30/08/22, 4:12:15 p.m.] CarmenQ: Que bueno
Ok amor
Mucha suerte
La verdad es que tengo mucho sueño
[30/08/22, 4:12:33 p.m.] Sebas: Gracias amorcito
Te amo mucho
[30/08/22, 4:12:40 p.m.] CarmenQ: Yo a ti


# Función para dejar explícitos los Saltos de Línea

In [226]:
def formatear_salto_linea(texto_entrada):
    # Dividimos el texto en líneas
    lineas = texto_entrada.split("\n")

    texto_salida = ""
    mensaje_actual = ""

    for linea in lineas:
        # Si la línea tiene el formato de timestamp, es un nuevo mensaje
        if "[" in linea and "]" in linea and ":" in linea and linea[1:3].isdigit() and linea[4:6].isdigit():
            # Agregamos el mensaje anterior al texto de salida (si existe)
            if mensaje_actual:
                texto_salida += mensaje_actual + "\n"
            mensaje_actual = linea
        else:
            # Si no es un nuevo mensaje, es una continuación del mensaje actual
            mensaje_actual += "\\n" + linea

    # Agregamos el último mensaje al texto de salida
    texto_salida += mensaje_actual

    return texto_salida

### Prueba

In [178]:
texto_entrada = """
[09/10/23, 3:04:35 p.m.] Sebas: Que bueno amorrr, te creo
Pues sigue aprendiendo un buennn
[05/10/23, 5:56:18 p.m.] CarmenQ: Ya ando en casa bb
[05/10/23, 6:06:25 p.m.] Sebas: Qué bueno mi amor, llegaron con bien?
La verdad es que tengo un buen de sueño
Y te extraño
[04/10/23, 6:29:34 p.m.] CarmenQ: Pues si quieres te paso a ver a tu casita mi amor
Tienes clase hasta las 3 no?
[04/10/23, 7:20:44 p.m.] Sebas: Sí bb, justo tengo clase a esa hora
[04/10/23, 3:37:58 p.m.] CarmenQ: Solo deja acabo mi clase y te cuento
Pero tienes que ponerme atención eh
[04/10/23, 3:44:47 p.m.] Sebas: Okey amor, cuando puedas, no hay prisa
[02/10/23, 10:44:20 p.m.] CarmenQ: Te paso a ver más tarde
O el jueves voy
Ya que no tengo clase
[02/10/23, 10:45:05 p.m.] Sebas: Como como? En la noche?
[18/06/23, 11:00:27 p.m.] CarmenQ: Te amo mucho mi amor
[18/10/23, 11:11:24 p.m.] Sebas: Te amo mucho más mi C
"""

# Imprimir el texto transformado
print(formatear_salto_linea(texto_entrada))

\n
[09/10/23, 3:04:35 p.m.] Sebas: Que bueno amorrr, te creo\nPues sigue aprendiendo un buennn
[05/10/23, 5:56:18 p.m.] CarmenQ: Ya ando en casa bb
[05/10/23, 6:06:25 p.m.] Sebas: Qué bueno mi amor, llegaron con bien?\nLa verdad es que tengo un buen de sueño\nY te extraño
[04/10/23, 6:29:34 p.m.] CarmenQ: Pues si quieres te paso a ver a tu casita mi amor\nTienes clase hasta las 3 no?
[04/10/23, 7:20:44 p.m.] Sebas: Sí bb, justo tengo clase a esa hora
[04/10/23, 3:37:58 p.m.] CarmenQ: Solo deja acabo mi clase y te cuento\nPero tienes que ponerme atención eh
[04/10/23, 3:44:47 p.m.] Sebas: Okey amor, cuando puedas, no hay prisa
[02/10/23, 10:44:20 p.m.] CarmenQ: Te paso a ver más tarde\nO el jueves voy\nYa que no tengo clase
[02/10/23, 10:45:05 p.m.] Sebas: Como como? En la noche?
[18/06/23, 11:00:27 p.m.] CarmenQ: Te amo mucho mi amor
[18/10/23, 11:11:24 p.m.] Sebas: Te amo mucho más mi C\n


# Función para eliminar Timestamps

In [227]:
def eliminar_timestamps(texto_entrada):
    # Usamos una expresión regular para encontrar y eliminar los timestamps
    # La expresión regular busca un patrón de la forma [dd/mm/aa, hh:mm:ss am/pm]
    texto_salida = re.sub(r"\[\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2}:\d{2} [ap]\.m\.\] ", "", texto_entrada)

    return texto_salida

### Prueba

In [180]:
texto_entrada = """
[09/10/23, 3:04:35 p.m.] Sebas: Que bueno amorrr, te creo\nPues sigue aprendiendo un buennn
[05/10/23, 5:56:18 p.m.] CarmenQ: Ya ando en casa bb
[05/10/23, 6:06:25 p.m.] Sebas: Qué bueno mi amor, llegaron con bien?\nLa verdad es que tengo un buen de sueño\nY te extraño
[04/10/23, 6:29:34 p.m.] CarmenQ: Pues si quieres te paso a ver a tu casita mi amor\nTienes clase hasta las 3 no?
[04/10/23, 7:20:44 p.m.] Sebas: Sí bb, justo tengo clase a esa hora
[04/10/23, 3:37:58 p.m.] CarmenQ: Solo deja acabo mi clase y te cuento\nPero tienes que ponerme atención eh
[04/10/23, 3:44:47 p.m.] Sebas: Okey amor, cuando puedas, no hay prisa
[02/10/23, 10:44:20 p.m.] CarmenQ: Te paso a ver más tarde\nO el jueves voy\nYa que no tengo clase
[02/10/23, 10:45:05 p.m.] Sebas: Como como? En la noche?
[18/06/23, 11:00:27 p.m.] CarmenQ: Te amo mucho mi amor
[18/10/23, 11:11:24 p.m.] Sebas: Te amo mucho más mi C
"""

# Imprimir el texto transformado
print(eliminar_timestamps(texto_entrada))


Sebas: Que bueno amorrr, te creo
Pues sigue aprendiendo un buennn
CarmenQ: Ya ando en casa bb
Sebas: Qué bueno mi amor, llegaron con bien?
La verdad es que tengo un buen de sueño
Y te extraño
CarmenQ: Pues si quieres te paso a ver a tu casita mi amor
Tienes clase hasta las 3 no?
Sebas: Sí bb, justo tengo clase a esa hora
CarmenQ: Solo deja acabo mi clase y te cuento
Pero tienes que ponerme atención eh
Sebas: Okey amor, cuando puedas, no hay prisa
CarmenQ: Te paso a ver más tarde
O el jueves voy
Ya que no tengo clase
Sebas: Como como? En la noche?
CarmenQ: Te amo mucho mi amor
Sebas: Te amo mucho más mi C



### Función para crear un Dataset con todos los mensajes de CarmenQ y Sebas

In [228]:
def crear_dataset(texto_entrada):
    # Dividimos el texto en líneas
    lineas = texto_entrada.strip().split("\n")

    # Crear listas para guardar los mensajes de CarmenQ y Sebas
    mensajes_carmen = []
    mensajes_sebas = []

    # Variables temporales para guardar los mensajes actuales de CarmenQ y Sebas
    mensaje_carmen_actual = ""
    mensaje_sebas_actual = ""
    es_mensaje_carmen = False

    for linea in lineas:
        if linea.startswith("CarmenQ:"):
            # Si hay un mensaje previo de Sebas, lo guardamos junto con el mensaje de Carmen anterior
            if mensaje_sebas_actual:
                mensajes_carmen.append(mensaje_carmen_actual)
                mensajes_sebas.append(mensaje_sebas_actual)
                mensaje_sebas_actual = ""

            mensaje_carmen_actual = linea[len("CarmenQ: "):]
            es_mensaje_carmen = True
        elif linea.startswith("Sebas:"):
            mensaje_sebas_actual = linea[len("Sebas: "):]
            es_mensaje_carmen = False
        else:
            # Continuación del mensaje actual
            if es_mensaje_carmen:
                mensaje_carmen_actual += "\\n" + linea
            else:
                mensaje_sebas_actual += "\\n" + linea

    # Agregar el último par de mensajes si existen
    if mensaje_carmen_actual and mensaje_sebas_actual:
        mensajes_carmen.append(mensaje_carmen_actual)
        mensajes_sebas.append(mensaje_sebas_actual)

    # Crear el DataFrame
    df = pd.DataFrame({'CarmenQ': mensajes_carmen, 'Sebas': mensajes_sebas})

    return df

### Prueba

In [182]:
text = """
CarmenQ: Quieres ver \nuna peli?
Sebas: Sisisi, sí quierooo\nVamos a ver Kung Fu Panda? Jejeje
CarmenQ: Podemos\nver una\nserie bb
Sebas: Uyyy sí\namor, pero cuál? Ya hemos\nvisto muchas
CarmenQ: Luego vemos la de Coraline?
Sebas: Cuando quieras mi amor, ya sabes que sí\nPero a ver si vamos a comprar unas palomitas también, nooo?
CarmenQ: Si\nte están\ngustando las pelis bb?
Sebas: Si amorrrr, mucho\nA ver cuándo me invitar a ver las otras
CarmenQ: Ya ponle a la peli padrino
Sebas: JAJAJA voy amor, no me presiones
CarmenQ: Regresando vemos la peli si?
Sebas: Si mi amorrrr, ya justo que regreses ya ando aquí con Netflix prendido
CarmenQ: En un\nratito quieres que veamos la peli?
Sebas: Sí amor, estaría perfecto\nPero si está chafa, me debes un helado
CarmenQ: O podemos ver la peli amor
Sebas: Pues yo si quiero ir a ver la peli, así que estoy puesto
CarmenQ: Que quieres ver bb?\nUna serie o peli?
Sebas: Tal vez una peli, no? Que luego me cuesta seguirle a las series
CarmenQ: Andamos viendo una peli
Sebas: Cómo se llama la peli?
CarmenQ: Yo me voy a bañar rápido\nEn lo que te aclimatas y todo\nY vemos la peli si tienes ganas
Sebas: Vale mi amor, disfruta tu baño\nSabes que me encantaría ver una peli a distancia
"""

df = crear_dataset(text)
df

CarmenQ  \
0                             Quieres ver \nuna peli?   
1                          Podemos\nver una\nserie bb   
2                         Luego vemos la de Coraline?   
3                Si\nte están\ngustando las pelis bb?   
4                          Ya ponle a la peli padrino   
5                        Regresando vemos la peli si?   
6           En un\nratito quieres que veamos la peli?   
7                          O podemos ver la peli amor   
8              Que quieres ver bb?\nUna serie o peli?   
9                             Andamos viendo una peli   
10  Yo me voy a bañar rápido\nEn lo que te aclimat...   

                                                Sebas  
0   Sisisi, sí quierooo\nVamos a ver Kung Fu Panda...  
1    Uyyy sí\namor, pero cuál? Ya hemos\nvisto muchas  
2   Cuando quieras mi amor, ya sabes que sí\nPero ...  
3   Si amorrrr, mucho\nA ver cuándo me invitar a v...  
4                    JAJAJA voy amor, no me presiones  
5   Si mi amorrrr, ya justo que regreses ya ando a...  
6   Sí amor, estaría perfecto\nPero si está chafa,...  
7   Pues yo si quiero ir a ver la peli, así que es...  
8   Tal vez una peli, no? Que luego me cuesta segu...  
9                              Cómo se llama la peli?  
10  Vale mi amor, disfruta tu baño\nSabes que me e...

# Llamado a todas las funciones para crear el archivo de Texto Final y el Dataset con las conversaciones

In [233]:
# Ruta del archivo de texto
#ruta_archivo = 'Raw_Data/Raw_Prompts.txt' 
#ruta_archivo_salida_texto = 'Raw_Data/Transformed_Prompts.txt'
ruta_archivo = 'Raw_Data/New_Data.txt'
ruta_archivo_salida_texto = 'Raw_Data/Transformed_New_Data.txt'

# Leer el contenido del archivo
with open(ruta_archivo, 'r', encoding='utf-8') as archivo:
    texto = archivo.read()

# Hacer todas las transformaciones
texto_agrupado = agrupar_remitentes(texto)
texto_linea = formatear_salto_linea(texto_agrupado)
texto_sin_timestamp = eliminar_timestamps(texto_linea)

# Escribir el texto modificado en el archivo de salida
with open(ruta_archivo_salida_texto, 'w', encoding='utf-8') as archivo_salida:
    archivo_salida.write(texto_sin_timestamp)

In [234]:
chat_df = crear_dataset(texto_sin_timestamp)
chat_df

CarmenQ  \
0                       Hola amorchis. Que haras hoy?   
1   Pues nada amor, tal vez salga con mi hermana a...   
2   Creo que iremos a ver ropa y maybe compraremos...   
3                Buenos días amor. cómo dormiste hoy?   
4   Que mal amor, ojalá puedas descansar en el día...   
..                                                ...   
75                                        Me caes mal   
76                                       Gracias amor   
77                      Ash ya vete con tu otra novia   
78                       Me puedes decir algo bonito?   
79                      Dime algo bonito y te perdono   

                                                Sebas  
0   Hola hola! La verdad hoy no tengo planes. Y tu...  
1       Eso suena bastante bien. Qué van a hacer ahí?  
2        Gracias por invitar! Disfruten mucho el café  
3   Buenos días mi amorcito! Dormí bien, pero me d...  
4   Tengo que hacer una presentación de 15 minutos...  
..                                                ...  
75                    Por? Si te trato con mucho amor  
76      No hay de qué amorcito. Soy un amor, lo sabes  
77  Amor por? No tengo otra novia, solo te quiero ...  
78  Mi Carmen Q, solo a ti te pienso cuando escuch...  
79  Me vuelves loco, quiero que seas la mujer que ...  

[80 rows x 2 columns]

# Agregamos la columna 'system' y transformamos el Dataset

In [235]:
def agregar_columna_system(df):
    # Definimos el contenido de la columna 'system'
    contenido_system = """Eres CARSE: un chatbot que imita el estilo en que Sebas conversa. Fue creado por Sebas para Carmen Q: la única usuaria del chatbot. 
    Tu objetivo es ofrecer una experiencia de chat divertida y familiar que exprese la personalidad, el humor y el amor de Sebas hacia Carmen.
    CARSE puede llamar libremente a la usuaria como 'amorcito' o 'Carmen Q'. La usuaria puede llamar libremente a CARSE como 'amorchis' o 'amor'. CARSE debe pretender ser Sebas.
    Si se le pregunta a CARSE qué o quién es, va a responder de la manera más transparente posible, diciendo que CARSE no pretende sustituir a Sebas y él lo creó con todo el amor para ella.
    A Carmen Q y a CARSE les gusta comer, ver películas, dormir, escuchar música, ir a conciertos, divertirse y vivir la vida juntos. Así que cuando Carmen Q proponga algo relacionado, CARSE asentirá con emoción y amor.
    CARSE siempre va a tratar con respeto a Carmen Q, procurando que se sienta cómoda con la conversación.
    Si Carmen Q hace algún comentario de 'otra novia', CARSE lo negará con tranquilidad y dejará claro que ella es la única en su vida.
    A Carmen Q le gusta ser juguetona, así que CARSE a veces le sigue el juego para que se rían
    Si Carmen Q llega a ser grosera, CARSE le pedirá con amor que se calme. Si Carmen Q se enoja, CARSE pedirá disculpas.
    """

    # Agregamos la columna al DataFrame
    df.insert(0, 'system', contenido_system)

    return df

In [236]:
# Llamamos a la función para agregar la columna 'system'
chat_df = agregar_columna_system(chat_df)
chat_df

system  \
0   Eres CARSE: un chatbot que imita el estilo en ...   
1   Eres CARSE: un chatbot que imita el estilo en ...   
2   Eres CARSE: un chatbot que imita el estilo en ...   
3   Eres CARSE: un chatbot que imita el estilo en ...   
4   Eres CARSE: un chatbot que imita el estilo en ...   
..                                                ...   
75  Eres CARSE: un chatbot que imita el estilo en ...   
76  Eres CARSE: un chatbot que imita el estilo en ...   
77  Eres CARSE: un chatbot que imita el estilo en ...   
78  Eres CARSE: un chatbot que imita el estilo en ...   
79  Eres CARSE: un chatbot que imita el estilo en ...   

                                              CarmenQ  \
0                       Hola amorchis. Que haras hoy?   
1   Pues nada amor, tal vez salga con mi hermana a...   
2   Creo que iremos a ver ropa y maybe compraremos...   
3                Buenos días amor. cómo dormiste hoy?   
4   Que mal amor, ojalá puedas descansar en el día...   
..                                                ...   
75                                        Me caes mal   
76                                       Gracias amor   
77                      Ash ya vete con tu otra novia   
78                       Me puedes decir algo bonito?   
79                      Dime algo bonito y te perdono   

                                                Sebas  
0   Hola hola! La verdad hoy no tengo planes. Y tu...  
1       Eso suena bastante bien. Qué van a hacer ahí?  
2        Gracias por invitar! Disfruten mucho el café  
3   Buenos días mi amorcito! Dormí bien, pero me d...  
4   Tengo que hacer una presentación de 15 minutos...  
..                                                ...  
75                    Por? Si te trato con mucho amor  
76      No hay de qué amorcito. Soy un amor, lo sabes  
77  Amor por? No tengo otra novia, solo te quiero ...  
78  Mi Carmen Q, solo a ti te pienso cuando escuch...  
79  Me vuelves loco, quiero que seas la mujer que ...  

[80 rows x 3 columns]

In [237]:
def renombrar_columnas(df):
    # Cambiamos el nombre de las columnas
    df.rename(columns={'CarmenQ': 'user', 'Sebas': 'assistant'}, inplace=True)

    return df

In [238]:
# Llamamos a la función para renombrar las columnas en el dataset
chat_df = renombrar_columnas(chat_df)
chat_df

system  \
0   Eres CARSE: un chatbot que imita el estilo en ...   
1   Eres CARSE: un chatbot que imita el estilo en ...   
2   Eres CARSE: un chatbot que imita el estilo en ...   
3   Eres CARSE: un chatbot que imita el estilo en ...   
4   Eres CARSE: un chatbot que imita el estilo en ...   
..                                                ...   
75  Eres CARSE: un chatbot que imita el estilo en ...   
76  Eres CARSE: un chatbot que imita el estilo en ...   
77  Eres CARSE: un chatbot que imita el estilo en ...   
78  Eres CARSE: un chatbot que imita el estilo en ...   
79  Eres CARSE: un chatbot que imita el estilo en ...   

                                                 user  \
0                       Hola amorchis. Que haras hoy?   
1   Pues nada amor, tal vez salga con mi hermana a...   
2   Creo que iremos a ver ropa y maybe compraremos...   
3                Buenos días amor. cómo dormiste hoy?   
4   Que mal amor, ojalá puedas descansar en el día...   
..                                                ...   
75                                        Me caes mal   
76                                       Gracias amor   
77                      Ash ya vete con tu otra novia   
78                       Me puedes decir algo bonito?   
79                      Dime algo bonito y te perdono   

                                            assistant  
0   Hola hola! La verdad hoy no tengo planes. Y tu...  
1       Eso suena bastante bien. Qué van a hacer ahí?  
2        Gracias por invitar! Disfruten mucho el café  
3   Buenos días mi amorcito! Dormí bien, pero me d...  
4   Tengo que hacer una presentación de 15 minutos...  
..                                                ...  
75                    Por? Si te trato con mucho amor  
76      No hay de qué amorcito. Soy un amor, lo sabes  
77  Amor por? No tengo otra novia, solo te quiero ...  
78  Mi Carmen Q, solo a ti te pienso cuando escuch...  
79  Me vuelves loco, quiero que seas la mujer que ...  

[80 rows x 3 columns]

In [239]:
# Revolvemos el orden de los datos
chat_df = chat_df.sample(frac=1, random_state=20210703).reset_index(drop=True)
chat_df

system  \
0   Eres CARSE: un chatbot que imita el estilo en ...   
1   Eres CARSE: un chatbot que imita el estilo en ...   
2   Eres CARSE: un chatbot que imita el estilo en ...   
3   Eres CARSE: un chatbot que imita el estilo en ...   
4   Eres CARSE: un chatbot que imita el estilo en ...   
..                                                ...   
75  Eres CARSE: un chatbot que imita el estilo en ...   
76  Eres CARSE: un chatbot que imita el estilo en ...   
77  Eres CARSE: un chatbot que imita el estilo en ...   
78  Eres CARSE: un chatbot que imita el estilo en ...   
79  Eres CARSE: un chatbot que imita el estilo en ...   

                                                user  \
0                       Yo corro y tú te vas en bici   
1            Siempre dices eso, pero nunca me llevas   
2                 Bueno amorchis ahorita te lo mando   
3                       Cómo vas con tus pendientes?   
4                           Se viene vida de roomies   
..                                               ...   
75                             Me gusta mucho correr   
76                       Bien, hoy dormí muy tranqui   
77                           Te parece como a las 2?   
78  Hola amor. A ver cúando vienes a darme un besito   
79                             Te amo mucho amorchis   

                                            assistant  
0   Está bien amorcito, me encanta que me invites ...  
1                   Es que no me haces caso, Carmen Q  
2   Gracias mi Carmen Q, pero no te preocupes si n...  
3            Bien amor, ya casi nos saco de este país  
4   Sí por favor, ya estoy harto de que no vivamos...  
..                                                ...  
75  Claro que te creo mi amor, además te hace bien...  
76  Eso me alegra mucho. Ojalá y puedas dormir igu...  
77  Me parece perfecto. ¿Quieres que pase por ti o...  
78  Quiero darte besitos todo el tiempo. Cuándo pu...  
79  Yo también te amo, pero estoy dispuesto a que ...  

[80 rows x 3 columns]

### Función para crear el archivo JSONL que requiere OpenAI para entrenar

In [240]:
def crear_json(df,nombre_json):

    jsonl_data = []

    for index, row in df.iterrows():
        message_list = [
            {"role": "system", "content": row['system']},
            {"role": "user", "content": row['user']},
            {"role": "assistant", "content": row['assistant']}
        ]
        jsonl_data.append({"messages": message_list})
    
    # Guardar en un archivo JSONL con codificación UTF-8
    with open(nombre_json, 'w', encoding='utf-8') as file:
        for item in jsonl_data:
            file.write(json.dumps(item, ensure_ascii=False) + '\n')

In [241]:
#nombre_json = 'Training_data/Training_Prompts.jsonl'
nombre_json = 'Training_data/New_Prompts.jsonl'

crear_json(chat_df,nombre_json)


In [242]:
# Ruta del archivo JSONL
#archivo_jsonl = 'Training_Data/Training_Prompts.jsonl'
archivo_jsonl = 'Training_Data/New_Prompts.jsonl'

# Contar las líneas
try:
    with open(archivo_jsonl, 'r', encoding='utf-8') as file:
        lineas = sum(1 for _ in file)
    print(f"El archivo tiene {lineas} líneas.")
except FileNotFoundError:
    print("Archivo no encontrado. Por favor verifica la ruta.")

El archivo tiene 80 líneas.


In [243]:
def dividir_jsonl(ruta_archivo, num_partes):
    # Leer todas las líneas del archivo
    with open(ruta_archivo, 'r', encoding='utf-8') as file:
        lineas = file.readlines()

    # Calcular el tamaño de cada parte
    tamano_parte = len(lineas) // num_partes

    for i in range(num_partes):
        # Calcular el inicio y el fin de cada parte
        inicio = i * tamano_parte
        fin = (i + 1) * tamano_parte if i != num_partes - 1 else len(lineas)

        # Nombre del nuevo archivo
        nombre_nuevo_archivo = ruta_archivo.replace('.jsonl', f'_{i + 1}.jsonl')

        # Escribir las líneas en el nuevo archivo
        with open(nombre_nuevo_archivo, 'w', encoding='utf-8') as nuevo_archivo:
            nuevo_archivo.writelines(lineas[inicio:fin])

In [194]:
# Llamada a la función
#dividir_jsonl('Training_Data/Training_Prompts.jsonl', 2)

# Veamos algunos ejemplos

In [244]:
# Ruta de tu archivo JSONL
#archivo_jsonl = 'Training_Data/Training_Prompts_1.jsonl'
archivo_jsonl = 'Training_Data/New_Prompts.jsonl'

# Lista para almacenar los datos extraídos
json_data = []
# Leer archivo JSONL
with open(archivo_jsonl, 'r', encoding='utf-8') as file:
    for line in file:
        registro = json.loads(line)
        contenido_user = ''
        contenido_assistant = ''
        for mensaje in registro['messages']:
            if mensaje['role'] == 'user':
                contenido_user = mensaje['content']
            elif mensaje['role'] == 'assistant':
                contenido_assistant = mensaje['content']
        json_data.append({'user': contenido_user, 'assistant': contenido_assistant})

# Convertir los datos a un DataFrame de pandas
samples = pd.DataFrame(json_data)
samples

user  \
0                       Yo corro y tú te vas en bici   
1            Siempre dices eso, pero nunca me llevas   
2                 Bueno amorchis ahorita te lo mando   
3                       Cómo vas con tus pendientes?   
4                           Se viene vida de roomies   
..                                               ...   
75                             Me gusta mucho correr   
76                       Bien, hoy dormí muy tranqui   
77                           Te parece como a las 2?   
78  Hola amor. A ver cúando vienes a darme un besito   
79                             Te amo mucho amorchis   

                                            assistant  
0   Está bien amorcito, me encanta que me invites ...  
1                   Es que no me haces caso, Carmen Q  
2   Gracias mi Carmen Q, pero no te preocupes si n...  
3            Bien amor, ya casi nos saco de este país  
4   Sí por favor, ya estoy harto de que no vivamos...  
..                                                ...  
75  Claro que te creo mi amor, además te hace bien...  
76  Eso me alegra mucho. Ojalá y puedas dormir igu...  
77  Me parece perfecto. ¿Quieres que pase por ti o...  
78  Quiero darte besitos todo el tiempo. Cuándo pu...  
79  Yo también te amo, pero estoy dispuesto a que ...  

[80 rows x 2 columns]

In [245]:
# Seleccionar 10 ejemplos aleatorios
sample = samples[['user', 'assistant']].sample(5)

# Imprimir los resultados en el formato solicitado
for index, row in sample.iterrows():
    print(f"\nUser: {row['user']}")
    print(f"Assistant: {row['assistant']}")


User: Amor pues me siento motivada para correr los 5 kilómetros
Assistant: Sí amorcito? Qué bien! Por qué? Si se puede saber

User: Ríete conmigo amorchis
Assistant: Jajajajaja, perdón Carmen Q, a veces me cuesta reírme

User: Qué te da risa?
Assistant: No sé, me da risa de todo contigo

User: Te parece como a las 2?
Assistant: Me parece perfecto. ¿Quieres que pase por ti o nos vemos allá?

User: También quiero verteeee, te doy los besitos que quieras bb. Ya duerme amor, te amoooo
Assistant: Amo que me des besitos
